# Women in Data Datathon -2025

## Project: SpaceAware – Traffic Heatmap Analysis  

**Team Name:** Data Divas  
**Team Members:**  
- Payton Maurer  
- Debisree Ray  
- Varshitha Venkatesh  
- Aiperi Subanova  

**Notebook Purpose:**  
This notebook takes CSV Data of 24 hours from UDL/ELSET and produces the Hourly animated Heatmap visualization to highlight the change in the hourly pattern.



### 1. Basic installations

In [1]:
!pip -q install gradio

In [2]:
!pip -q install pandas numpy python-dateutil

In [3]:
# === Hourly animated heatmap from looker_heatmap_points.csv (Folium) ===
!pip -q install folium

In [4]:
# ---------- deps ----------
!pip -q install folium ipywidgets


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 9.2 MB/s eta 0:00:00


### 2. Import Libraries

In [5]:
# 1.4 Imports
import warnings
warnings.filterwarnings('ignore')


import pandas as pd, numpy as np, folium, branca
from folium.plugins import HeatMapWithTime
from IPython.display import display, HTML, clear_output
import ipywidgets as w
from datetime import datetime, timezone

import os, glob, math
from datetime import datetime, timedelta, timezone
import numpy as np
import pandas as pd

import os, numpy as np, pandas as pd
import folium, branca
from folium.plugins import HeatMapWithTime
from IPython.display import HTML, display

import os

from folium.plugins import HeatMapWithTime
import gradio as gr

import os, numpy as np, pandas as pd
import folium
from folium.plugins import HeatMap
import branca
from IPython.display import HTML, display
import ipywidgets as w

pd.set_option('display.max_columns', None)


print("✅ Imports loaded")

✅ Imports loaded


### 3. Access Google Drive for mounting

In [6]:
# ---------------- CONFIG (edit if needed) ----------------
# Time window for propagation:
GLOBAL_START_ISO   = None                 # e.g., "2025-09-14T00:00:00Z" or None to start at row epoch
GLOBAL_END_ISO     = None                 # e.g., "2025-09-14T06:00:00Z" or None to use MAX_HOURS_PER_SAT
MAX_HOURS_PER_SAT  = 6.0                  # used only if GLOBAL_END_ISO is None
STEP_MINUTES       = 10

In [7]:
 # ---- Mount Drive and locate the folder containing vis.ipynb ----
from google.colab import drive
drive.mount("/content/drive", force_remount=True)

# Try to discover the folder where vis.ipynb lives
candidates = glob.glob("/content/drive/MyDrive/**/vis.ipynb", recursive=True)
if candidates:
    BASE_DIR = os.path.dirname(candidates[0])
else:
    BASE_DIR = "/content/drive/MyDrive"   # fallback; set manually if needed
    print("⚠️ Could not auto-locate vis.ipynb. Using BASE_DIR =", BASE_DIR)

INPUT_CSV  = os.path.join(BASE_DIR, "elset_source_data.csv")
OUTPUT_CSV = os.path.join(BASE_DIR, "looker_heatmap_points.csv")

if not os.path.isfile(INPUT_CSV):
    raise FileNotFoundError(f"Could not find {INPUT_CSV}. Place 'elset_source_data.csv' next to vis.ipynb.")

print("Using BASE_DIR:", BASE_DIR)
print("Reading:", os.path.basename(INPUT_CSV))
print("Writing:", os.path.basename(OUTPUT_CSV))

Mounted at /content/drive
Using BASE_DIR: /content/drive/MyDrive/WID_Datathon/Debisree_Heatmap_Appilcation
Reading: elset_source_data.csv
Writing: looker_heatmap_points.csv


### 4. Calculatuion

* This section reads the UDL Elset Data (Downloaded prior through bulk data download request, and saved as a csv file)

* Calculates essential parameters like longitude/latitude form the raw parameters in the Elset Data.

* Saves the output file - a quick overview of the output dataframe is also shown below.

In [8]:
# ======================================================================
# UDL ELSET -> points for heatmaps, with rich filter fields
# ======================================================================



# Propagation window: default = each elset's epoch .. epoch + MAX_HOURS_PER_SAT
GLOBAL_START_ISO   = None                     # e.g. "2025-09-13T00:00:00Z" or None
GLOBAL_END_ISO     = None                     # e.g. "2025-09-14T00:00:00Z" or None
MAX_HOURS_PER_SAT  = 6.0                      # used when GLOBAL_END_ISO is None
STEP_MINUTES       = 10                       # sampling cadence (shorter => more points)

# ---- WGS-84 & gravity ----
MU_EARTH   = 398600.4418            # km^3 / s^2
R_EARTH    = 6378.137               # km (equatorial radius)
F_EARTH    = 1.0 / 298.257223563
E2         = F_EARTH * (2 - F_EARTH)

# ---------- helpers ----------
def parse_utc(s):
    if s is None or (isinstance(s, float) and np.isnan(s)): return None
    s = str(s).strip()
    if not s: return None
    try:
        if s.endswith("Z"):
            s2 = s[:-1]
            try:
                dt = datetime.fromisoformat(s2)
            except ValueError:
                return pd.to_datetime(s, utc=True).to_pydatetime()
            return dt.replace(tzinfo=timezone.utc)
        dt = datetime.fromisoformat(s)
        if dt.tzinfo is None: dt = dt.replace(tzinfo=timezone.utc)
        return dt.astimezone(timezone.utc)
    except Exception:
        try:
            return pd.to_datetime(s, utc=True).to_pydatetime()
        except Exception:
            return None

def kepler_E_from_M(M, e, tol=1e-10, max_iter=50):
    # Solve M = E - e*sin(E) for E (radians)
    M = (M + 2*math.pi) % (2*math.pi)
    E = M if e < 0.8 else math.pi
    for _ in range(max_iter):
        f = E - e*math.sin(E) - M
        fp = 1 - e*math.cos(E)
        dE = -f / fp
        E += dE
        if abs(dE) < tol: break
    return E

def gmst_approx(dt_utc):
    # Simple GMST (radians) — good for visualization
    epoch = datetime(2000, 1, 1, 12, 0, 0, tzinfo=timezone.utc)  # J2000
    dt = (dt_utc - epoch).total_seconds()
    JD = 2451545.0 + dt / 86400.0
    T = (JD - 2451545.0) / 36525.0
    gmst_sec = (67310.54841 +
                (876600.0 * 3600 + 8640184.812866) * T +
                0.093104 * T**2 -
                6.2e-6 * T**3)
    return (gmst_sec % 86400.0) * (2 * math.pi / 86400.0)

def eci_to_ecef(r_eci, gmst_rad):
    x, y, z = r_eci
    cg, sg = math.cos(gmst_rad), math.sin(gmst_rad)
    return np.array([ cg*x + sg*y, -sg*x + cg*y, z ])

def ecef_to_geodetic(r_ecef):
    x, y, z = r_ecef
    lon = math.atan2(y, x)
    p = math.hypot(x, y)
    lat = math.atan2(z, p * (1 - E2))
    for _ in range(10):
        sin_lat = math.sin(lat)
        N = R_EARTH / math.sqrt(1 - E2 * sin_lat**2)
        alt = p / math.cos(lat) - N
        lat_new = math.atan2(z, p * (1 - E2 * (N / (N + alt))))
        if abs(lat - lat_new) < 1e-12:
            lat = lat_new
            break
        lat = lat_new
    sin_lat = math.sin(lat)
    N = R_EARTH / math.sqrt(1 - E2 * sin_lat**2)
    alt = p / math.cos(lat) - N
    lat_deg = math.degrees(lat)
    lon_deg = ((math.degrees(lon) + 180) % 360) - 180
    return lat_deg, lon_deg, alt

def revday_to_a_km(n_revday):
    if n_revday is None or n_revday <= 0: return np.nan
    n_rad_s = 2 * math.pi * n_revday / 86400.0
    return (MU_EARTH / (n_rad_s**2))**(1.0 / 3.0)

def elements_to_r_eci(a_km, e, inc_deg, raan_deg, argp_deg, M0_deg, dt_sec):
    # Two-body propagation: elements at epoch -> ECI position at epoch+dt
    n = math.sqrt(MU_EARTH / (a_km**3))  # rad/s
    M = math.radians(M0_deg) + n * dt_sec
    E = kepler_E_from_M(M, e)
    nu = 2 * math.atan2(math.sqrt(1 + e) * math.sin(E / 2.0),
                        math.sqrt(1 - e) * math.cos(E / 2.0))
    r_mag = a_km * (1 - e * math.cos(E))
    r_pqw = np.array([r_mag * math.cos(nu), r_mag * math.sin(nu), 0.0])

    i  = math.radians(inc_deg)
    O  = math.radians(raan_deg)
    w  = math.radians(argp_deg)
    cO, sO = math.cos(O), math.sin(O)
    cw, sw = math.cos(w), math.sin(w)
    ci, si = math.cos(i), math.sin(i)

    # R3(O) * R1(i) * R3(w)
    R = np.array([
        [ cO*cw - sO*sw*ci, -cO*sw - sO*cw*ci,  sO*si],
        [ sO*cw + cO*sw*ci, -sO*sw + cO*cw*ci, -cO*si],
        [        sw*si     ,         cw*si     ,   ci ]
    ])
    return R @ r_pqw

def pick(colset, *names):
    for n in names:
        if n in colset:
            return n
    return None

# -------- derived, filter-friendly helpers --------
def orbit_class_from_alt(alt_km):
    if pd.isna(alt_km): return "Unknown"
    if alt_km < 2000: return "LEO"
    if 2000 <= alt_km <= 35686: return "MEO"
    if abs(alt_km - 35786) <= 300: return "GEO"
    if alt_km > 35686: return "HEO"
    return "Unknown"

def inc_band(deg):
    if pd.isna(deg): return "Unknown"
    if deg < 20: return "Equatorial (<20°)"
    if deg < 60: return "Mid-lat (20–60°)"
    return "High/Polar (≥60°)"

def raan_bin_15(raan_deg):
    if pd.isna(raan_deg): return "Unknown"
    low = int(math.floor(raan_deg/15.0)*15)
    high = low + 15
    return "{}–{}°".format(low, high)

def lat_band(lat):
    if pd.isna(lat): return "Unknown"
    a = abs(lat)
    if a < 20: return "Equatorial (|lat|<20)"
    if a < 60: return "Mid-lat (20–60)"
    return "Polar (≥60)"

def safe_alt_km(x):
    try:
        return float(x)
    except:
        return np.nan

# ---- Read CSV  ----
if not os.path.isfile(INPUT_CSV):
    raise FileNotFoundError("Cannot find {}".format(INPUT_CSV))

df_raw = pd.read_csv(INPUT_CSV)
present = set(df_raw.columns)

# Columns (aliases supported)
col_sat   = pick(present, "satNo", "sat_id", "idOnOrbit", "catalogNumber", "norad", "noradid")
col_inc   = pick(present, "inclination")
col_raan  = pick(present, "raan", "RAAN", "rightAscensionOfAscendingNode")
col_argp  = pick(present, "argOfPerigee", "argumentOfPerigee", "aop")
col_M     = pick(present, "meanAnomaly", "M")
col_n     = pick(present, "meanMotion", "n")
col_e     = pick(present, "eccentricity", "e")
col_a     = pick(present, "semiMajorAxis", "semi_major_axis", "a")
col_epoch = pick(present, "effectiveFrom", "epoch", "elsetEpoch", "epochUtc", "createdAt")

# Useful provenance fields (pass-through if present)
pass_through_cols = [c for c in [
    pick(present, "dataMode"),
    pick(present, "ephemType"),
    pick(present, "source"),
    pick(present, "origin"),
    pick(present, "algorithm"),
    pick(present, "uct"),
    pick(present, "createdAt")
] if c is not None]

required = [col_inc, col_raan, col_argp, col_M, col_n, col_e, col_epoch]
if any(v is None for v in required):
    raise ValueError("CSV missing required fields (need RAAN and standard elset fields). Present: {}".format(sorted(present)))

# Canonical rename
rename_map = {}
if col_sat:   rename_map[col_sat]   = "satNo"
rename_map[col_inc]   = "inclination"
rename_map[col_raan]  = "raan"
rename_map[col_argp]  = "argOfPerigee"
rename_map[col_M]     = "meanAnomaly"
rename_map[col_n]     = "meanMotion"
rename_map[col_e]     = "eccentricity"
rename_map[col_epoch] = "epoch"
if col_a:     rename_map[col_a]     = "semiMajorAxis"
for c in pass_through_cols:
    # keep same name
    rename_map[c] = c

df = df_raw.rename(columns=rename_map)

# Types
for c in ["satNo","inclination","raan","argOfPerigee","meanAnomaly","meanMotion","eccentricity","semiMajorAxis"]:
    if c in df.columns:
        df[c] = pd.to_numeric(df[c], errors="coerce")
df["epoch"] = df["epoch"].apply(parse_utc)

# Keep only valid rows
essentials = ["inclination","raan","argOfPerigee","meanAnomaly","meanMotion","eccentricity","epoch"]
mask_ok = np.ones(len(df), dtype=bool)
for c in essentials:
    mask_ok &= df[c].notna().values
df = df.loc[mask_ok].reset_index(drop=True)
if df.empty:
    raise ValueError("No valid ELSET rows after cleaning.")

# Window
start_g = parse_utc(GLOBAL_START_ISO) if GLOBAL_START_ISO else None
end_g   = parse_utc(GLOBAL_END_ISO)   if GLOBAL_END_ISO   else None
step = timedelta(minutes=STEP_MINUTES)

def a_for_row(row):
    if "semiMajorAxis" in df.columns and pd.notna(row["semiMajorAxis"]):
        return float(row["semiMajorAxis"])
    return revday_to_a_km(float(row["meanMotion"]))

# -------- propagate & assemble rich rows --------
rows = []
for _, r in df.iterrows():
    # ID
    try:
        sat_id = int(r["satNo"]) if "satNo" in df.columns and pd.notna(r["satNo"]) else ""
    except Exception:
        sat_id = ""

    inc, raan, argp = float(r["inclination"]), float(r["raan"]), float(r["argOfPerigee"])
    M0, nrd, ecc    = float(r["meanAnomaly"]), float(r["meanMotion"]), float(r["eccentricity"])
    a_km = a_for_row(r)
    if not np.isfinite(a_km) or a_km <= 0:
        continue

    # derived orbit geometry
    period_min = 1440.0 / nrd if nrd and nrd > 0 else np.nan
    apogee_radius_km  = a_km * (1 + ecc)
    perigee_radius_km = a_km * (1 - ecc)
    apogee_alt_km  = apogee_radius_km  - R_EARTH
    perigee_alt_km = perigee_radius_km - R_EARTH

    inc_band_val  = inc_band(inc)
    raan_bin_val  = raan_bin_15(raan)

    # provenance snapshot (same for all samples of this elset)
    passthru_vals = {}
    for c in pass_through_cols:
        passthru_vals[c] = r.get(c)

    epoch = r["epoch"]
    if epoch is None:
        continue

    t0 = start_g or epoch
    if t0 < epoch: t0 = epoch
    t1 = end_g or (epoch + timedelta(hours=MAX_HOURS_PER_SAT))
    if t1 <= t0: continue

    t = t0
    while t <= t1:
        dt_sec = (t - epoch).total_seconds()
        gmst = gmst_approx(t)

        r_eci  = elements_to_r_eci(a_km, ecc, inc, raan, argp, M0, dt_sec)
        r_ecef = eci_to_ecef(r_eci, gmst)
        lat, lon, alt_km = ecef_to_geodetic(r_ecef)
        alt_km = safe_alt_km(alt_km)

        # time-derived filters
        t_utc = t.astimezone(timezone.utc)
        ts_iso = t_utc.isoformat().replace("+00:00","Z")
        hour_utc = t_utc.hour
        date_utc = t_utc.date().isoformat()
        dow_utc  = t_utc.strftime("%A")

        # instant-derived filters
        hemi = "Northern" if lat >= 0 else "Southern"
        lat_band_val = lat_band(lat)
        orbit_class  = orbit_class_from_alt(alt_km)

        row_out = {
            # core heatmap fields
            "sat_id": sat_id,
            "timestamp": ts_iso,
            "latitude": round(float(lat), 6),
            "longitude": round(float(lon), 6),
            "altitude_km": round(float(alt_km), 3),

            # useful filters (time)
            "date_utc": date_utc,
            "hour_utc": hour_utc,
            "dow_utc": dow_utc,

            # useful filters (instant geography)
            "hemisphere": hemi,
            "lat_band": lat_band_val,
            "orbit_class": orbit_class,

            # useful filters (orbit params; constant through this elset)
            "inclination": inc,
            "inclination_band": inc_band_val,
            "raan": raan,
            "raan_bin_15": raan_bin_val,
            "eccentricity": ecc,
            "meanMotion": nrd,                   # rev/day
            "period_min": period_min,            # minutes
            "semiMajorAxis_km": a_km,
            "perigee_alt_km": perigee_alt_km,
            "apogee_alt_km": apogee_alt_km,
        }

        # include provenance if present
        row_out.update(passthru_vals)

        rows.append(row_out)
        t += step

# ---- make DataFrame & write ----
out = pd.DataFrame(rows)

# enforce numeric dtypes where expected
for c in ["latitude","longitude","altitude_km","inclination","raan","eccentricity",
          "meanMotion","period_min","semiMajorAxis_km","perigee_alt_km","apogee_alt_km","hour_utc"]:
    if c in out.columns:
        out[c] = pd.to_numeric(out[c], errors="coerce")

# sanity: keep valid lat/lon ranges
out = out[(out["latitude"].between(-90,90)) & (out["longitude"].between(-180,180))].copy()

out.to_csv(OUTPUT_CSV, index=False)
print("✅ Wrote {:,} rows to {}".format(len(out), OUTPUT_CSV))
print("📄 Columns:", list(out.columns))

# quick peek
display(out.head())


✅ Wrote 1,459,095 rows to /content/drive/MyDrive/WID_Datathon/Debisree_Heatmap_Appilcation/looker_heatmap_points.csv
📄 Columns: ['sat_id', 'timestamp', 'latitude', 'longitude', 'altitude_km', 'date_utc', 'hour_utc', 'dow_utc', 'hemisphere', 'lat_band', 'orbit_class', 'inclination', 'inclination_band', 'raan', 'raan_bin_15', 'eccentricity', 'meanMotion', 'period_min', 'semiMajorAxis_km', 'perigee_alt_km', 'apogee_alt_km', 'dataMode', 'ephemType', 'source', 'origin', 'algorithm', 'uct', 'createdAt']


sat_id                    timestamp  latitude   longitude  altitude_km  \
0   38358  2025-09-14T00:00:02.000160Z -5.070081 -176.451703      551.857   
1   38358  2025-09-14T00:10:02.000160Z -6.046324 -141.142100      548.141   
2   38358  2025-09-14T00:20:02.000160Z -4.496218 -105.836374      546.016   
3   38358  2025-09-14T00:30:02.000160Z -1.073698  -70.758882      546.482   
4   38358  2025-09-14T00:40:02.000160Z  2.791684  -35.783660      549.477   

     date_utc  hour_utc dow_utc hemisphere               lat_band orbit_class  \
0  2025-09-14         0  Sunday   Southern  Equatorial (|lat|<20)         LEO   
1  2025-09-14         0  Sunday   Southern  Equatorial (|lat|<20)         LEO   
2  2025-09-14         0  Sunday   Southern  Equatorial (|lat|<20)         LEO   
3  2025-09-14         0  Sunday   Southern  Equatorial (|lat|<20)         LEO   
4  2025-09-14         0  Sunday   Northern  Equatorial (|lat|<20)         LEO   

   inclination   inclination_band      raan raan_bin_15  eccentricity  \
0       6.0273  Equatorial (<20°)  300.1559    300–315°       0.00092   
1       6.0273  Equatorial (<20°)  300.1559    300–315°       0.00092   
2       6.0273  Equatorial (<20°)  300.1559    300–315°       0.00092   
3       6.0273  Equatorial (<20°)  300.1559    300–315°       0.00092   
4       6.0273  Equatorial (<20°)  300.1559    300–315°       0.00092   

   meanMotion  period_min  semiMajorAxis_km  perigee_alt_km  apogee_alt_km  \
0   15.047901    95.69441          6930.287      545.777047     558.522953   
1   15.047901    95.69441          6930.287      545.777047     558.522953   
2   15.047901    95.69441          6930.287      545.777047     558.522953   
3   15.047901    95.69441          6930.287      545.777047     558.522953   
4   15.047901    95.69441          6930.287      545.777047     558.522953   

  dataMode  ephemType     source  origin algorithm  uct  \
0     REAL        NaN  18th SPCS     NaN      SGP4  NaN   
1     REAL        NaN  18th SPCS     NaN      SGP4  NaN   
2     REAL        NaN  18th SPCS     NaN      SGP4  NaN   
3     REAL        NaN  18th SPCS     NaN      SGP4  NaN   
4     REAL        NaN  18th SPCS     NaN      SGP4  NaN   

                  createdAt  
0  2025-09-14T04:07:56.371Z  
1  2025-09-14T04:07:56.371Z  
2  2025-09-14T04:07:56.371Z  
3  2025-09-14T04:07:56.371Z  
4  2025-09-14T04:07:56.371Z

### 5. Heatmap Generation - single heatmap - for 24 hours

### Not the Final One - just a trial, how the heatmap would like


In [9]:


# --- settings you can tweak ---
CSV_NAME = "looker_heatmap_points.csv"   # path to your generated output
USE_ALTITUDE_AS_WEIGHT = False           # True → altitude-weighted intensity; False → pure density
MAX_POINTS = 250_000                     # downsample for responsiveness
RADIUS = 16                              # try 12–24
BLUR   = 22                              # try 18–26

# --- find CSV (wd first, then MyDrive in Colab) ---
csv_path = CSV_NAME
if not os.path.exists(csv_path):
    try:
        import google.colab  # type: ignore
        from google.colab import drive
        drive.mount("/content/drive", force_remount=True)
        for root, _, files in os.walk("/content/drive/MyDrive"):
            if CSV_NAME in files:
                csv_path = os.path.join(root, CSV_NAME); break
    except Exception:
        pass
if not os.path.exists(csv_path):
    raise FileNotFoundError(f"Couldn't find {CSV_NAME}. Set CSV_NAME to the correct path.")

print("Using CSV:", csv_path)

# --- load & clean ---
df = pd.read_csv(csv_path)
if df.empty:
    raise ValueError("CSV has 0 rows. Re-run the generator with a wider time window.")

for c in ("latitude","longitude","altitude_km"):
    if c in df.columns:
        df[c] = pd.to_numeric(df[c], errors="coerce")

df = df.dropna(subset=["latitude","longitude"])
df = df[(df["latitude"].between(-90,90)) & (df["longitude"].between(-180,180))].copy()

if len(df) > MAX_POINTS:
    df = df.sample(MAX_POINTS, random_state=42).reset_index(drop=True)
    print(f"Downsampled to {len(df):,} points.")

# weights
df["weight"] = 1.0
weight_caption = "Relative density"
if USE_ALTITUDE_AS_WEIGHT and "altitude_km" in df.columns:
    q1, q99 = df["altitude_km"].quantile([0.01, 0.99])
    w = (df["altitude_km"].clip(q1, q99) - q1) / max(1e-9, (q99 - q1))
    df["weight"] = (w * 0.85) + 0.15
    weight_caption = "Relative density (altitude-weighted)"

# center + time window text (UTC)
center = [float(df["latitude"].median()), float(df["longitude"].median())]
start_txt, end_txt = "?", "?"
if "timestamp" in df.columns:
    ts = pd.to_datetime(df["timestamp"], errors="coerce", utc=True)
    if ts.notna().any():
        tmin, tmax = ts.min(), ts.max()
        start_txt = tmin.strftime("%Y-%m-%d %H:%MZ")
        end_txt   = tmax.strftime("%Y-%m-%d %H:%MZ")

# --- map ---
m = folium.Map(location=center, zoom_start=2, tiles="CartoDB dark_matter", control_scale=True)

# yellow→red gradient (dark low → yellow high)
gradient = {
    0.00: "#1a0000",  # very dark maroon
    0.20: "#4d0000",
    0.40: "#a00000",
    0.70: "#ff4500",
    1.00: "#ffff66"   # warm yellow glow
}

HeatMap(
    data=df[["latitude","longitude","weight"]].itertuples(index=False, name=None),
    radius=RADIUS,
    blur=BLUR,
    max_zoom=5,
    min_opacity=0.25,
    gradient=gradient
).add_to(m)

# --- colorbar/legend (cmap) bottom-right ---
cmap = branca.colormap.LinearColormap(
    colors=[gradient[k] for k in sorted(gradient.keys())],
    index=[0.0, 0.2, 0.4, 0.7, 1.0],
    vmin=0, vmax=1
).to_step(5)
cmap.caption = weight_caption
cmap.add_to(m)

# --- top overlay: time window banner (non-blocking, above the map) ---
title_html = f"""
<div style="
  position: fixed; top: 10px; left: 50%; transform: translateX(-50%);
  z-index: 9999; pointer-events: none;
  background: rgba(0,0,0,0.65); color: #fff;
  padding: 6px 12px; border-radius: 6px; font-size: 14px; font-weight: 600;
  box-shadow: 0 0 8px rgba(0,0,0,0.35);
  ">
  Time window (UTC): {start_txt} → {end_txt}
</div>
"""
m.get_root().html.add_child(folium.Element(title_html))

# save + render inline
out_html = "heatmap_styled.html"
m.save(out_html)
display(HTML(m.get_root().render()))
print(f"✅ Saved polished map to {out_html}")


Mounted at /content/drive
Using CSV: /content/drive/MyDrive/WID_Datathon/Debisree_Heatmap_Appilcation/looker_heatmap_points.csv
Downsampled to 250,000 points.


✅ Saved polished map to heatmap_styled.html


In [10]:
from google.colab import files
files.download("heatmap_styled.html")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### 6. The Final Animated Heatmap animation - showcasing hourly rate.

* Wrapped in Gradio - by clicking the link, the application can be accessed in the browser.
* Bunch of slicers and filters are available to narrow down the specific heatmap of interest.

In [13]:
# ==== UDL hourly heatmap — Gradio app with slicers; custom JS animation over leaflet-heat ====


# ---------- SETTINGS ----------
CSV_NAME = "looker_heatmap_points.csv"   # path/filename to output CSV
MAX_POINTS_PER_FRAME = 30_000            # downsample cap per hour for responsiveness
DEFAULT_RADIUS = 12                      # 12–20 is good globally
DEFAULT_BLUR   = 13
DEFAULT_TILES  = "CartoDB dark_matter"   # change to "OpenStreetMap" if tiles are blocked

# yellow→red gradient (same as your static)
GRADIENT = {0.00:"#1a0000", 0.20:"#4d0000", 0.40:"#a00000", 0.70:"#ff4500", 1.00:"#ffff66"}

# ---------- robust CSV resolver ----------
def _resolve_csv(path_hint: str, basename: str) -> str:
    if os.path.isfile(path_hint): return path_hint
    # try Colab drive
    try:
        from google.colab import drive as _drive  # type: ignore
        if not os.path.isdir("/content/drive"):
            _drive.mount("/content/drive", force_remount=False)
    except Exception:
        pass
    for c in [basename, f"./{basename}", f"/content/{basename}",
              f"/content/drive/MyDrive/{basename}",
              f"/content/drive/MyDrive/Colab Notebooks/{basename}"]:
        if os.path.isfile(c): return c
    # last-resort search (can be slow)
    if os.path.isdir("/content/drive"):
        for root, _, files in os.walk("/content/drive"):
            if basename in files: return os.path.join(root, basename)
    raise FileNotFoundError(f"Could not find '{basename}'. Put it next to the notebook or set CSV_NAME to a full path.")

CSV_PATH = _resolve_csv(CSV_NAME, os.path.basename(CSV_NAME))
print("✅ Using CSV:", CSV_PATH)

# ---------- LOAD ----------
df = pd.read_csv(CSV_PATH, low_memory=False)
if df.empty:
    raise ValueError("CSV has 0 rows.")

# types
for c in ("latitude","longitude","altitude_km","satNo","inclination","raan"):
    if c in df.columns:
        df[c] = pd.to_numeric(df[c], errors="coerce")

df = df.dropna(subset=["latitude","longitude"]).copy()
df = df[(df["latitude"].between(-90,90)) & (df["longitude"].between(-180,180))]

# pick a time column (prefer 'timestamp')
time_col = None
for cand in ("timestamp","epoch","effectiveFrom","createdAt"):
    if cand in df.columns:
        time_col = cand; break
if time_col is None:
    raise ValueError("No timestamp-like column found. Expected one of: timestamp, epoch, effectiveFrom, createdAt.")

df["__t"] = pd.to_datetime(df[time_col], errors="coerce", utc=True)
df = df.loc[df["__t"].notna()].copy()
df["__hbin"] = df["__t"].dt.floor("1H")

# sat_id fallback
if "sat_id" not in df.columns and "satNo" in df.columns:
    df["sat_id"] = df["satNo"].astype("Int64").astype(str)

# slicer option lists
hours_list = sorted(df["__hbin"].unique())
if not hours_list: raise ValueError("No hourly timestamps found in CSV.")
sat_options  = sorted(df.get("sat_id", pd.Series(dtype=str)).dropna().astype(str).unique().tolist())[:500]
orbit_opts   = sorted(df.get("orbit_class", pd.Series(dtype=str)).dropna().unique().tolist())
raan_opts    = sorted(df.get("raan_bin_15", pd.Series(dtype=str)).dropna().unique().tolist())

inc_min = float(np.nanmin(df["inclination"])) if "inclination" in df else 0.0
inc_max = float(np.nanmax(df["inclination"])) if "inclination" in df else 180.0
alt_min = float(np.nanmin(df["altitude_km"])) if "altitude_km" in df else 0.0
alt_max = float(np.nanmax(df["altitude_km"])) if "altitude_km" in df else 40000.0

def hour_label(dt):
    return pd.to_datetime(dt).strftime("%Y-%m-%d %H:00Z")

# ---------- helpers ----------
def normalize_series_0_1(s: pd.Series):
    if s.empty: return s
    q1, q99 = s.quantile([0.01, 0.99])
    denom = max(1e-9, (q99 - q1))
    return (s.clip(q1, q99) - q1) / denom

def filter_df(lo_idx, hi_idx, sat_ids, orbit_classes, raan_bins, inc_lo, inc_hi, alt_lo, alt_hi):
    lo = int(max(0, min(lo_idx, hi_idx)))
    hi = int(min(len(hours_list)-1, max(lo_idx, hi_idx)))
    hours_sel = set(hours_list[lo:hi+1])
    d = df[df["__hbin"].isin(hours_sel)].copy()
    if d.empty: return d
    if sat_ids and "sat_id" in d: d = d[d["sat_id"].astype(str).isin(sat_ids)]
    if orbit_classes and "orbit_class" in d: d = d[d["orbit_class"].isin(orbit_classes)]
    if raan_bins and "raan_bin_15" in d: d = d[d["raan_bin_15"].isin(raan_bins)]
    if "inclination" in d: d = d[(d["inclination"] >= inc_lo) & (d["inclination"] <= inc_hi)]
    if "altitude_km" in d: d = d[(d["altitude_km"] >= alt_lo) & (d["altitude_km"] <= alt_hi)]
    d = d[(d["latitude"].between(-90, 90)) & (d["longitude"].between(-180, 180))]
    return d

def make_frames(dsel, weight_mode, max_points):
    frames, labels, sizes = [], [], []
    for h, g in dsel.groupby("__hbin", sort=True):
        if len(g) == 0: continue
        if len(g) > max_points: g = g.sample(max_points, random_state=42)
        # per-frame weights: Count -> 1.0; Altitude-weighted -> normalized altitude per frame
        if weight_mode == "Altitude-weighted" and "altitude_km" in g.columns:
            wf = normalize_series_0_1(g["altitude_km"]) * 0.8 + 0.2  # map to [0.2, 1.0]
        else:
            wf = pd.Series(1.0, index=g.index)
        g = g.assign(weight=wf.fillna(0.5))
        g = g.dropna(subset=["latitude","longitude","weight"])
        pts = np.column_stack([
            g["latitude"].astype(float).values,
            g["longitude"].astype(float).values,
            g["weight"].clip(0.2,1.0).astype(float).values
        ]).tolist()
        if not pts: continue
        frames.append(pts)
        labels.append(hour_label(h))
        sizes.append(len(pts))
    return frames, labels, sizes

def render_map(dsel, radius, blur, tiles, weight_mode, debug_markers=False):
    if dsel.empty:
        return "<div style='color:#e33;padding:8px'>No data after filtering.</div>", "No data.", None

    frames, labels, sizes = make_frames(dsel, weight_mode, MAX_POINTS_PER_FRAME)
    if not frames:
        return "<div style='color:#e33;padding:8px'>No hourly frames produced.</div>", "No frames.", None

    center = [float(dsel["latitude"].median()), float(dsel["longitude"].median())]
    m = folium.Map(location=center, zoom_start=2, tiles=tiles, control_scale=True)

    # Ensure leaflet-heat is loaded by adding a tiny, hidden HeatMap
    HeatMap([[0.0,0.0,0.01]], radius=1, blur=1, max_zoom=5).add_to(m)

    # Optional debug markers
    if debug_markers and frames[0]:
        for lat, lon, _ in frames[0][:400]:
            folium.CircleMarker([lat, lon], radius=2, color="#ffaa00",
                                fill=True, fill_opacity=0.9, opacity=0.9).add_to(m)

    # Legend
    cmap = branca.colormap.LinearColormap(
        colors=[GRADIENT[k] for k in sorted(GRADIENT.keys())],
        index=[0.0,0.2,0.4,0.7,1.0], vmin=0, vmax=1
    ).to_step(5)
    cmap.caption = "Relative density" + (" (altitude-weighted)" if weight_mode == "Altitude-weighted" else "")
    cmap.add_to(m)

    # Top banner
    banner = (
        '<div id="udl-banner" style="position:fixed;top:10px;left:50%;transform:translateX(-50%);'
        'z-index:9999;pointer-events:none;background:rgba(0,0,0,.65);color:#fff;padding:6px 12px;'
        'border-radius:6px;font-size:14px;font-weight:600;box-shadow:0 0 8px rgba(0,0,0,.35);">'
        'Hourly animation (UTC): ' + labels[0] + ' → ' + labels[-1] +
        ' &nbsp;|&nbsp; Frame: <span id="udl-frame-lbl">1</span> / ' + str(len(labels)) +
        '</div>'
    )
    m.get_root().html.add_child(folium.Element(banner))

    # JS controls + animation (NO f-strings; concat variables safely)
    gradient_items = sorted(GRADIENT.items(), key=lambda kv: float(kv[0]))
    gradient_js_pairs = ",".join([str(k) + ":" + json.dumps(v) for k, v in gradient_items])

    controls_html = (
        '<div id="udl-controls" style="position:fixed;bottom:14px;left:50%;transform:translateX(-50%);'
        'z-index:9999;background:rgba(0,0,0,.55);color:#fff;padding:8px 12px;border-radius:8px;'
        'display:flex;align-items:center;gap:10px;box-shadow:0 0 8px rgba(0,0,0,.35);">'
        '<button id="udl-play" style="cursor:pointer;">▶︎</button>'
        '<button id="udl-pause" style="cursor:pointer;">❚❚</button>'
        '<input id="udl-slider" type="range" min="0" max="' + str(len(labels)-1) + '" value="0" step="1" style="width:420px;">'
        '<span id="udl-time" style="font-weight:600;"></span>'
        '</div>'
        '<script>'
        'const FRAMES = ' + json.dumps(frames) + ';'
        'const LABELS = ' + json.dumps(labels) + ';'
        'const RADIUS = ' + str(int(radius)) + ';'
        'const BLUR   = ' + str(int(blur)) + ';'
        'const GRADIENT = {' + gradient_js_pairs + '};'
        'const INTERVAL_MS = 1100;'
        'function findMapVar(){ const keys = Object.keys(window).filter(k=>k.startsWith("map_")).sort();'
        ' return keys.length ? window[keys[keys.length-1]] : null; }'
        'function whenReady(checkFn, onOk, tries){ if(tries<=0){return;}'
        ' if(checkFn()){ onOk(); return; } setTimeout(()=>whenReady(checkFn,onOk,tries-1),50); }'
        'function init(){ const MAP = findMapVar(); if(!MAP || !window.L || !L.heatLayer){ return false; }'
        ' let heat = L.heatLayer(FRAMES[0], {radius:RADIUS, blur:BLUR, gradient:GRADIENT}).addTo(MAP);'
        ' const slider=document.getElementById("udl-slider");'
        ' const timeLbl=document.getElementById("udl-time");'
        ' const frameLbl=document.getElementById("udl-frame-lbl");'
        ' const btnPlay=document.getElementById("udl-play");'
        ' const btnPause=document.getElementById("udl-pause");'
        ' function render(i){ i=Math.max(0, Math.min(FRAMES.length-1, i));'
        '   heat.setLatLngs(FRAMES[i]); timeLbl.textContent = LABELS[i]; if(frameLbl) frameLbl.textContent = (i+1).toString(); }'
        ' render(0);'
        ' slider.addEventListener("input", e => { render(parseInt(e.target.value)); });'
        ' let timer=null;'
        ' function play(){ if(timer) return; timer=setInterval(()=>{ let i=parseInt(slider.value); i=(i+1)%FRAMES.length; slider.value=i; render(i); }, INTERVAL_MS); }'
        ' function pause(){ if(timer){ clearInterval(timer); timer=null; } }'
        ' btnPlay.addEventListener("click", play); btnPause.addEventListener("click", pause);'
        ' play(); return true; }'
        'whenReady(()=>!!findMapVar() && !!window.L && !!L.heatLayer, init, 400);'
        '</script>'
    )
    m.get_root().html.add_child(folium.Element(controls_html))

    html_str = m.get_root().render()
    out_path = "udl_heatmap_animation.html"
    with open(out_path, "w", encoding="utf-8") as f:
        f.write(html_str)

    iframe_html = '<iframe srcdoc="' + html_str.replace('"','&quot;').replace('\n',' ') + '" style="width:100%;height:640px;border:0;"></iframe>'
    stat = "Frames: {} • pts/hour (min/med/max): {}/{}/{} • saved: {}".format(
        len(frames), min(sizes), int(np.median(sizes)), max(sizes), out_path
    )
    return iframe_html, stat, out_path

# ---------- Gradio UI (full slicers on top) ----------
with gr.Blocks(title="UDL Hourly Heatmap (Animated)") as demo:
    gr.Markdown("## UDL Hourly Heatmap — Animated (no TimeDimension)")

    with gr.Accordion("Filters", open=True):
        with gr.Row():
            hour_start = gr.Slider(minimum=0, maximum=len(hours_list)-1, step=1, value=0,
                                   label=f"Hour start index (0 → {hour_label(hours_list[0])})")
            hour_end   = gr.Slider(minimum=0, maximum=len(hours_list)-1, step=1, value=len(hours_list)-1,
                                   label=f"Hour end index ({len(hours_list)-1} → {hour_label(hours_list[-1])})")
        with gr.Row():
            sat_ids = gr.Dropdown(choices=sat_options, value=None, multiselect=True, label="Satellite IDs (optional)")
            orbit_classes = gr.Dropdown(choices=orbit_opts, value=None, multiselect=True, label="Orbit class (optional)")
            raan_bins = gr.Dropdown(choices=raan_opts, value=None, multiselect=True, label="RAAN 15° bin (optional)")
        with gr.Row():
            inc_lo = gr.Slider(minimum=max(0.0, inc_min-1), maximum=min(180.0, inc_max+1), step=0.5, value=inc_min, label="Inclination° MIN")
            inc_hi = gr.Slider(minimum=max(0.0, inc_min-1), maximum=min(180.0, inc_max+1), step=0.5, value=inc_max, label="Inclination° MAX")
        with gr.Row():
            alt_lo = gr.Slider(minimum=max(0.0, alt_min-50), maximum=alt_max+50, step=10, value=alt_min, label="Altitude km MIN")
            alt_hi = gr.Slider(minimum=max(0.0, alt_min-50), maximum=alt_max+50, step=10, value=alt_max, label="Altitude km MAX")
        with gr.Row():
            weight_mode = gr.Radio(choices=["Count","Altitude-weighted"], value="Count", label="Weight mode")
            radius = gr.Slider(minimum=6, maximum=22, step=1, value=DEFAULT_RADIUS, label="Kernel radius")
            blur   = gr.Slider(minimum=8, maximum=28, step=1, value=DEFAULT_BLUR, label="Blur")
            tiles  = gr.Dropdown(choices=["CartoDB dark_matter","OpenStreetMap","CartoDB positron","Stamen Terrain"],
                                 value=DEFAULT_TILES, label="Basemap")
            debug_markers = gr.Checkbox(value=False, label="Debug markers (first frame)")

    go_btn = gr.Button("Render animation", variant="primary")
    status = gr.Markdown()
    map_html = gr.HTML(value="", label="Heatmap (interactive)")
    map_file = gr.File(label="Download HTML", file_count="single")

    def run_render(h_start, h_end, sat, orb, raan, lo_i, hi_i, lo_a, hi_a, wmode, rad, blr, tile_choice, dbg):
        lo_idx, hi_idx = int(min(h_start, h_end)), int(max(h_start, h_end))
        inc_lo_sel, inc_hi_sel = float(min(lo_i, hi_i)), float(max(lo_i, hi_i))
        alt_lo_sel, alt_hi_sel = float(min(lo_a, hi_a)), float(max(lo_a, hi_a))
        dsel = filter_df(lo_idx, hi_idx, sat or [], orb or [], raan or [],
                         inc_lo_sel, inc_hi_sel, alt_lo_sel, alt_hi_sel)
        return render_map(dsel, int(rad), int(blr), tile_choice, wmode, debug_markers=bool(dbg))

    go_btn.click(
        fn=run_render,
        inputs=[hour_start, hour_end, sat_ids, orbit_classes, raan_bins, inc_lo, inc_hi, alt_lo, alt_hi,
                weight_mode, radius, blur, tiles, debug_markers],
        outputs=[map_html, status, map_file]
    )

demo.launch(server_name="0.0.0.0", server_port=None, share=True)


✅ Using CSV: /content/drive/MyDrive/WID_Datathon/Debisree_Heatmap_Appilcation/looker_heatmap_points.csv
Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://bfe401c1a1cf173625.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
